In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Stroke"
cohort = "GSE161533"

# Input paths
in_trait_dir = "../../input/GEO/Stroke"
in_cohort_dir = "../../input/GEO/Stroke/GSE161533"

# Output paths
out_data_file = "../../output/preprocess/Stroke/GSE161533.csv"
out_gene_data_file = "../../output/preprocess/Stroke/gene_data/GSE161533.csv"
out_clinical_data_file = "../../output/preprocess/Stroke/clinical_data/GSE161533.csv"
json_path = "../../output/preprocess/Stroke/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Expression data from esophageal squamous cell carcinoma patients"
!Series_summary	"we conducted microarray experiments of 28 stage I-III ESCC patients based on Affymetrix Gene Chip Human Genome U133 plus 2.0 Array, performed enrichment analysis of differentially expressed genes (DEGs) as well as gene set enrichment analysis of all valid genes. Moreover, we summarized the secreted protein-encoding DEGs as well as esophagus-specific DEGs, hoping to offer some hints for early diagnosis and target for more efficacious treatment for ESCC in near future."
!Series_overall_design	"In total, there were 84 paired  normal tissues, paratumor tissues, and tumor tissues from 28 ESCC patients were chosen to perform microarray analysis."
Sample Characteristics Dictionary:
{0: ['tissue: normal tissue', 'tissue: paratumor tissue', 'tissue: tumor tissue'], 1: ['Stage: IB', 'Stage: I', 'Stage: IA', 'Stage: IIA', 'Stage: IIB', 'Stage: II', 'Stage: IIIA', 'Stage: IIIB'

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
import pandas as pd
import numpy as np
import os
import re
from typing import Optional, Callable, Dict, Any

# Create a DataFrame from the sample characteristics dictionary provided in the previous step
sample_characteristics = {
    0: ['tissue: normal tissue', 'tissue: paratumor tissue', 'tissue: tumor tissue'], 
    1: ['Stage: IB', 'Stage: I', 'Stage: IA', 'Stage: IIA', 'Stage: IIB', 'Stage: II', 'Stage: IIIA', 'Stage: IIIB'], 
    2: ['age: 56', 'age: 57', 'age: 51', 'age: 64', 'age: 54', 'age: 73', 'age: 61', 'age: 71', 'age: 65', 'age: 60', 'age: 69', 'age: 63', 'age: 67', 'age: 70', 'age: 53', 'age: 75', 'age: 74'], 
    3: ['gender: Male', 'gender: Female'], 
    4: ['smoking history: None', 'smoking history: 30 years', 'smoking history: 20 years', 'smoking history: 36 years', 'smoking history: 50 years', 'smoking history: 40 years'], 
    5: ['drinking history: None', 'drinking history: Seldom', 'drinking history: 36 years', 'drinking history: 40 years', 'drinking history: 50 years'], 
    6: ['disease history: None', 'disease history: Hypertension', 'disease history: Breast cancer', 'disease history: Cerebral  infarction', 'disease history: Lymphoma', 'disease history: Hypertension, coronary heart disease, cerebral  infarction'], 
    7: ['family history of cancer: ESCC', 'family history of cancer: None', 'family history of cancer: lung cancer', 'family history of cancer: liver cancer', 'family history of cancer: none', 'family history of cancer: Colorectal cancer', 'family history of cancer: Gastric cancer', 'family history of cancer: cancer']
}

# Convert sample characteristics dictionary to a DataFrame to use with geo_select_clinical_features
clinical_data = pd.DataFrame.from_dict(sample_characteristics, orient='index')

# 1. Gene Expression Data Availability
# Affymetrix Gene Chip Human Genome U133 plus 2.0 Array is a gene expression microarray
is_gene_available = True

# 2.1 Data Availability
# Checking if stroke-related data is available in the sample characteristics
# The disease history field (index 6) contains "Cerebral infarction" which is related to stroke
trait_row = 6  # Disease history contains stroke-related information
age_row = 2    # Age information is available
gender_row = 3 # Gender information is available

# 2.2 Data Type Conversion Functions
def convert_trait(value: str) -> Optional[int]:
    """
    Convert disease history to binary stroke status.
    1 if cerebral infarction (stroke) is mentioned, 0 otherwise.
    """
    if pd.isna(value) or not isinstance(value, str):
        return None
    
    # Extract value after colon
    if ":" in value:
        value = value.split(":", 1)[1].strip()
    
    # Check if cerebral infarction is mentioned
    if "cerebral infarction" in value.lower():
        return 1
    else:
        return 0

def convert_age(value: str) -> Optional[float]:
    """
    Convert age string to numeric value.
    """
    if pd.isna(value) or not isinstance(value, str):
        return None
    
    # Extract value after colon
    if ":" in value:
        value = value.split(":", 1)[1].strip()
    
    # Extract numeric age
    match = re.search(r'\d+', value)
    if match:
        return float(match.group())
    else:
        return None

def convert_gender(value: str) -> Optional[int]:
    """
    Convert gender string to binary: 0 for female, 1 for male.
    """
    if pd.isna(value) or not isinstance(value, str):
        return None
    
    # Extract value after colon
    if ":" in value:
        value = value.split(":", 1)[1].strip()
    
    # Convert to binary
    if "male" in value.lower() and "female" not in value.lower():
        return 1
    elif "female" in value.lower():
        return 0
    else:
        return None

# 3. Save Metadata
# Check if trait data is available (trait_row is not None)
is_trait_available = trait_row is not None

# Validate and save cohort info
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
if trait_row is not None:
    # Extract clinical features using the geo_select_clinical_features function
    clinical_features_df = geo_select_clinical_features(
        clinical_df=clinical_data,
        trait=trait,
        trait_row=trait_row,
        convert_trait=convert_trait,
        age_row=age_row,
        convert_age=convert_age,
        gender_row=gender_row,
        convert_gender=convert_gender
    )
    
    # Preview the extracted clinical features
    preview = preview_df(clinical_features_df)
    print("Preview of clinical features:")
    print(preview)
    
    # Create directory if it doesn't exist
    os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
    
    # Save the clinical features to CSV
    clinical_features_df.to_csv(out_clinical_data_file, index=False)
    print(f"Clinical features saved to {out_clinical_data_file}")


Preview of clinical features:
{0: [0.0, 56.0, 1.0], 1: [0.0, 57.0, 0.0], 2: [0.0, 51.0, nan], 3: [0.0, 64.0, nan], 4: [0.0, 54.0, nan], 5: [0.0, 73.0, nan], 6: [nan, 61.0, nan], 7: [nan, 71.0, nan], 8: [nan, 65.0, nan], 9: [nan, 60.0, nan], 10: [nan, 69.0, nan], 11: [nan, 63.0, nan], 12: [nan, 67.0, nan], 13: [nan, 70.0, nan], 14: [nan, 53.0, nan], 15: [nan, 75.0, nan], 16: [nan, 74.0, nan]}
Clinical features saved to ../../output/preprocess/Stroke/clinical_data/GSE161533.csv


### Step 3: Gene Data Extraction

In [4]:
# 1. Get the SOFT and matrix file paths again 
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)
print(f"Matrix file found: {matrix_file}")

# 2. Use the get_genetic_data function from the library to get the gene_data
try:
    gene_data = get_genetic_data(matrix_file)
    print(f"Gene data shape: {gene_data.shape}")
    
    # 3. Print the first 20 row IDs (gene or probe identifiers)
    print("First 20 gene/probe identifiers:")
    print(gene_data.index[:20])
except Exception as e:
    print(f"Error extracting gene data: {e}")


Matrix file found: ../../input/GEO/Stroke/GSE161533/GSE161533_series_matrix.txt.gz


Gene data shape: (54675, 84)
First 20 gene/probe identifiers:
Index(['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at', '1294_at',
       '1316_at', '1320_at', '1405_i_at', '1431_at', '1438_at', '1487_at',
       '1494_f_at', '1552256_a_at', '1552257_a_at', '1552258_at', '1552261_at',
       '1552263_at', '1552264_a_at', '1552266_at'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# Looking at the gene identifiers, they appear to be Affymetrix probe IDs (like '1007_s_at', '1053_at') 
# rather than standard human gene symbols (which would look like BRCA1, TP53, etc.)
# These probe IDs need to be mapped to human gene symbols for meaningful analysis

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Analyze the gene annotation dataframe to identify which columns contain the gene identifiers and gene symbols
print("\nGene annotation preview:")
print(f"Columns in gene annotation: {gene_annotation.columns.tolist()}")
print(preview_df(gene_annotation, n=5))

# Let's look for platform information in the SOFT file to understand the annotation better
print("\nSearching for platform information in SOFT file:")
with gzip.open(soft_file, 'rt') as f:
    for i, line in enumerate(f):
        if '!Series_platform_id' in line:
            print(line.strip())
            break
        if i > 100:  # Limit search to first 100 lines
            print("Platform ID not found in first 100 lines")
            break

# Check if the SOFT file includes any reference to gene symbols
print("\nSearching for gene symbol information in SOFT file:")
with gzip.open(soft_file, 'rt') as f:
    gene_symbol_lines = []
    for i, line in enumerate(f):
        if 'GENE_SYMBOL' in line or 'gene_symbol' in line.lower() or 'symbol' in line.lower():
            gene_symbol_lines.append(line.strip())
        if i > 1000 and len(gene_symbol_lines) > 0:  # Limit search but ensure we found something
            break
    
    if gene_symbol_lines:
        print("Found references to gene symbols:")
        for line in gene_symbol_lines[:5]:  # Show just first 5 matches
            print(line)
    else:
        print("No explicit gene symbol references found in first 1000 lines")

# Look for alternative annotation files or references in the directory
print("\nChecking for additional annotation files in the directory:")
all_files = os.listdir(in_cohort_dir)
print([f for f in all_files if 'annotation' in f.lower() or 'platform' in f.lower() or 'gpl' in f.lower()])



Gene annotation preview:
Columns in gene annotation: ['ID', 'GB_ACC', 'SPOT_ID', 'Species Scientific Name', 'Annotation Date', 'Sequence Type', 'Sequence Source', 'Target Description', 'Representative Public ID', 'Gene Title', 'Gene Symbol', 'ENTREZ_GENE_ID', 'RefSeq Transcript ID', 'Gene Ontology Biological Process', 'Gene Ontology Cellular Component', 'Gene Ontology Molecular Function']
{'ID': ['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at'], 'GB_ACC': ['U48705', 'M87338', 'X51757', 'X69699', 'L36861'], 'SPOT_ID': [nan, nan, nan, nan, nan], 'Species Scientific Name': ['Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens'], 'Annotation Date': ['Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014'], 'Sequence Type': ['Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence'], 'Sequence Source': ['Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database', 'GenBank', 

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Identify columns for mapping
# Based on the preview of gene annotation data, we can see:
# - 'ID' column contains probe IDs (e.g., '1007_s_at') which match the gene expression data indices
# - 'Gene Symbol' column contains the human gene symbols we need (e.g., 'DDR1 /// MIR4640')

# 2. Get gene mapping dataframe
gene_mapping = get_gene_mapping(gene_annotation, prob_col='ID', gene_col='Gene Symbol')
print(f"Gene mapping shape: {gene_mapping.shape}")
print("Gene mapping sample (first 5 rows):")
print(gene_mapping.head())

# 3. Apply gene mapping to convert probe-level data to gene-level data
gene_data = apply_gene_mapping(gene_data, gene_mapping)
print(f"After mapping: Gene expression data shape: {gene_data.shape}")
print("First 10 gene symbols after mapping:")
print(gene_data.index[:10])

# Save the gene data to CSV
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data.to_csv(out_gene_data_file)
print(f"Gene expression data saved to {out_gene_data_file}")


Gene mapping shape: (45782, 2)
Gene mapping sample (first 5 rows):
          ID              Gene
0  1007_s_at  DDR1 /// MIR4640
1    1053_at              RFC2
2     117_at             HSPA6
3     121_at              PAX8
4  1255_g_at            GUCA1A
After mapping: Gene expression data shape: (21278, 84)
First 10 gene symbols after mapping:
Index(['A1BG', 'A1BG-AS1', 'A1CF', 'A2M', 'A2M-AS1', 'A2ML1', 'A2MP1',
       'A4GALT', 'A4GNT', 'AA06'],
      dtype='object', name='Gene')


Gene expression data saved to ../../output/preprocess/Stroke/gene_data/GSE161533.csv


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize gene symbols
print(f"Original gene data shape: {gene_data.shape}")

try:
    # Attempt to normalize gene symbols
    gene_data_normalized = normalize_gene_symbols_in_index(gene_data)
    print(f"Normalized gene data shape: {gene_data_normalized.shape}")
except Exception as e:
    print(f"Gene normalization failed: {e}")
    # If normalization fails, use the original gene data
    gene_data_normalized = gene_data.copy()
    print(f"Using original gene data with shape: {gene_data_normalized.shape}")

# Save the gene expression data 
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data_normalized.to_csv(out_gene_data_file)
print(f"Gene expression data saved to {out_gene_data_file}")

# 2. Load the clinical data from Step 2
# Get the clinical data from the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# Define conversion functions as in Step 2
def convert_trait(value: str) -> Optional[int]:
    """Convert disease history to binary stroke status (1 if cerebral infarction is mentioned, 0 otherwise)"""
    if pd.isna(value) or not isinstance(value, str):
        return None
    # Extract value after colon
    if ":" in value:
        value = value.split(":", 1)[1].strip()
    # Check if cerebral infarction is mentioned
    if "cerebral infarction" in value.lower():
        return 1
    else:
        return 0

def convert_age(value: str) -> Optional[float]:
    """Convert age string to numeric value"""
    if pd.isna(value) or not isinstance(value, str):
        return None
    # Extract value after colon
    if ":" in value:
        value = value.split(":", 1)[1].strip()
    # Extract numeric age
    match = re.search(r'\d+', value)
    if match:
        return float(match.group())
    else:
        return None

def convert_gender(value: str) -> Optional[int]:
    """Convert gender string to binary (0 for female, 1 for male)"""
    if pd.isna(value) or not isinstance(value, str):
        return None
    # Extract value after colon
    if ":" in value:
        value = value.split(":", 1)[1].strip()
    # Convert to binary
    if "male" in value.lower() and "female" not in value.lower():
        return 1
    elif "female" in value.lower():
        return 0
    else:
        return None

# Extract clinical features using the correct trait_row (6 for disease history)
clinical_features = geo_select_clinical_features(
    clinical_data, 
    trait=trait, 
    trait_row=6,  # Using disease history which contains cerebral infarction (stroke) information
    convert_trait=convert_trait,
    age_row=2,  # Age information
    convert_age=convert_age,
    gender_row=3,  # Gender information
    convert_gender=convert_gender
)

print(f"Clinical features shape: {clinical_features.shape}")
print("Clinical features preview:")
print(clinical_features.head())

# Save the clinical data
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
clinical_features.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# 3. Link clinical and genetic data
linked_data = geo_link_clinical_genetic_data(clinical_features, gene_data_normalized)
print(f"Linked data shape: {linked_data.shape}")
print("Linked data preview (first 5 rows, 5 columns):")
print(linked_data.iloc[:5, :5])

# 4. Handle missing values
linked_data_clean = handle_missing_values(linked_data, trait)
print(f"Linked data shape after handling missing values: {linked_data_clean.shape}")

# 5. Check for bias in the dataset
is_biased, linked_data_clean = judge_and_remove_biased_features(linked_data_clean, trait)

# 6. Conduct final quality validation
is_usable = validate_and_save_cohort_info(
    is_final=True,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=True,
    is_trait_available=True,
    is_biased=is_biased,
    df=linked_data_clean,
    note="Dataset contains gene expression data from esophageal squamous cell carcinoma patients. The 'Stroke' trait was extracted from disease history field, identifying patients with cerebral infarction as stroke cases."
)

# 7. Save the linked data if it's usable
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    linked_data_clean.to_csv(out_data_file, index=True)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Dataset deemed not usable for associative studies. Linked data not saved.")

Original gene data shape: (21278, 84)
Normalized gene data shape: (19845, 84)


Gene expression data saved to ../../output/preprocess/Stroke/gene_data/GSE161533.csv
Clinical features shape: (3, 84)
Clinical features preview:
        GSM4909553  GSM4909554  GSM4909555  GSM4909556  GSM4909557  \
Stroke         0.0         0.0         0.0         0.0         0.0   
Age           56.0        57.0        51.0        64.0        54.0   
Gender         1.0         1.0         1.0         0.0         1.0   

        GSM4909558  GSM4909559  GSM4909560  GSM4909561  GSM4909562  ...  \
Stroke         0.0         0.0         0.0         0.0         0.0  ...   
Age           64.0        73.0        73.0        61.0        71.0  ...   
Gender         0.0         0.0         1.0         1.0         1.0  ...   

        GSM4909627  GSM4909628  GSM4909629  GSM4909630  GSM4909631  \
Stroke         0.0         0.0         0.0         0.0         0.0   
Age           64.0        57.0        67.0        70.0        53.0   
Gender         1.0         1.0         1.0         1.0         

Linked data shape: (84, 19848)
Linked data preview (first 5 rows, 5 columns):
            Stroke   Age  Gender     A1BG  A1BG-AS1
GSM4909553     0.0  56.0     1.0  20.7429   21.2433
GSM4909554     0.0  57.0     1.0  14.0490   16.5552
GSM4909555     0.0  51.0     1.0  12.3174   16.3096
GSM4909556     0.0  64.0     0.0  17.3028   19.4446
GSM4909557     0.0  54.0     1.0  16.6225   14.8843


Linked data shape after handling missing values: (84, 19848)
Quartiles for 'Stroke':
  25%: 0.0
  50% (Median): 0.0
  75%: 0.0
Min: 0.0
Max: 0.0
The distribution of the feature 'Stroke' in this dataset is severely biased.

Quartiles for 'Age':
  25%: 59.25
  50% (Median): 64.0
  75%: 69.25
Min: 51.0
Max: 75.0
The distribution of the feature 'Age' in this dataset is fine.

For the feature 'Gender', the least common label is '0.0' with 21 occurrences. This represents 25.00% of the dataset.
The distribution of the feature 'Gender' in this dataset is fine.

Dataset deemed not usable for associative studies. Linked data not saved.
